In [1]:
# imports
import numpy as np
import scipy as sc
import scipy.linalg as scl
import plotly.graph_objects as go
import plotly.express as px

# Projekt 4 in Numerik 2,  Aufgabe 1
Janike Katter, Felix Reichling

## Aufgabe 1: QR-Verfahren

In [2]:
# Beispiel Matrizen:
A = np.matrix('5 4 2; 0 1 -1; -1 -1 3', dtype=float)
B = np.matrix('-1 1 3; 3 3 -2; -5 2 7', dtype=float)
C = np.matrix('-5 -10 -10 5; 4 16 11 -8; 12 13 8 -4; 22 48 28 -19', dtype=float)
D = np.matrix('0 0 0 1; 0 0 -1 0; 0 1 0 0; -1 0 0 0', dtype=float)

### Einfaches QR-Verfahren

In [3]:
def qr_fehler(M):
  err = 0
  mm = 0
  for i in range(len(M)):
    for j in range(len(M[0])):
      if not j >= i:
        err += abs(M[i,j])
        mm += 1

  return err/mm

In [4]:
def qr1(M, tol=1e-3, maxIter=1000000):
  AI = M
  err = qr_fehler(AI)
  errs = []
  errs.append(err)
  iteration = 0
  while (err > tol) and (iteration < maxIter):
    iteration += 1
    Q, R = scl.qr(AI)
    AI = np.matmul(R,Q)
    err = qr_fehler(AI)
    errs.append(err)
    #if iteration%10 == 0:
      #print(f"curr err: {err}")

  eigs = []
  for x in range(len(AI)):
    eigs.append(AI[x,x])


  return eigs, errs

### QR-Verfahren mit Shift

In [5]:
import scipy.optimize as sco

In [6]:
def qr_fehler2(M):
  z = len(M)-1
  err1 = 0
  err2 = 0
  m1 = 0
  m2 = 0
  for i in range(z):
    if i < z-1:
      err1 += abs(M[z,i])
      m1 += 1
      err2 += abs(M[z,i])
      err2 += abs(M[z-1,i])
      m2 += 2
    if i == z-1:
      err1 += abs(M[z,i])
      m1 += 1
  if m2 == 0:
    m2 = 1
    err2 = 10
  if len(M) == 2:
    err2 = 0
  return (err1/m1, err2/m2)


In [7]:
def qrshiftstep(M, tol=1e-3, maxIter=10000):
  AI = M
  errs = []
  err = qr_fehler2(AI)
  errs.append(err)
  iteration = 0
  while (err[0] > tol) and (err[1] > tol) and (iteration < maxIter):
    s = AI[-1,-1]
    n,m = AI.shape
    IM = np.eye(n,m)*s
    DI = AI-IM
    Q, R = scl.qr(DI)
    AI = np.matmul(R,Q)+IM 
    err = qr_fehler2(AI)
    errs.append(err)
    iteration += 1

  msg = 0
  if iteration > maxIter:
    if err[1] > tol:
      msg = -1
  return AI, errs, msg

In [8]:
def shorten_matrix(M, tol=1e-3):
  n,m = M.shape
  wegrows = 0
  eigvals = []
  err_real, err_imag = qr_fehler2(M)
  if err_real < tol:
    for r in reversed(range(n)):
      kannWeg = True
      for x in range(m-1):
        if not abs(M[r,x]) < tol:
          kannWeg = False
      if kannWeg:
        wegrows += 1
        eigvals.append(M[r,r])
      else:
        break
    if wegrows == 0:
      return M, None
    else:
      nn, nm = n-wegrows, m-wegrows
      if nn == 0:
        nn = 1
      if nm == 0:
        nm = 1
      NM = M[:nn,:nm]
      return NM, eigvals
  else:
    NM = M[:n-2,:m-2]
    R = M[n-2:,m-2:]
    aa = 1
    bb = (-R[1,1]-R[0,0])
    cc = R[0,0]*R[1,1]-R[1,0]*R[0,1]
    vorne = -bb/(2*aa)
    unterroot = bb**2-4*aa*cc
    hinten = sc.sqrt(unterroot)/(2*aa)
    print(f'a:{aa} b:{bb}, c:{cc}, vorne:{vorne}, unterWurzel:{unterroot}, hinten:{hinten}')
    eigvals.append(vorne+hinten)
    eigvals.append(vorne-hinten)
    return NM, eigvals
  print("Error: shorten_matrix should never end up here")
  return M, eigvals

In [9]:
def qr2(M, tol=1e-3, maxIter=10000):
  n,m = M.shape
  ende = False 
  AI = M
  errors = []
  eigvals = []
  while not ende:
    AI, errs, msg = qrshiftstep(AI, tol, maxIter)
    if msg == -1:
      print('No convergence for tolerance. Now breaking')
      return 0,0
    #print(f'qrshiftsteps: {AI}')
    AI, vals = shorten_matrix(AI)
    #print(f'curr vals: {vals}')
    if not len(vals) > 0:
      print(f'Critical Error, no eigenvalues')
      ende = True
    else:
      #print(f'curr: {AI}')
      eigvals.extend(vals)
      errors.extend(errs)
      n,m = AI.shape
      if (n <= 1) or (m <= 1):
        if (n==1) or (m == 1):
          eigvals.append(AI[0,0])
        ende = True
  return eigvals, errors


### QR-Verfahren mit oberer Hessenbergform

In [10]:
import math

In [11]:
def householderspiegelung(M):
  n,m = M.shape
  vec = M[1:,0].transpose()
  housevector = vec + math.copysign(scl.norm(vec), vec[0,0])*np.eye(1, n-1)
  scal = 2/ np.dot(housevector, housevector.transpose())
  M[1,0] = math.copysign(scl.norm(vec), -1*vec[0,0])
  for i in range(2,m):
    M[i,0] = 0
  vecs = np.array([])
  for z in range(1,n):
    vector = M[1:,z].transpose()
    vector_ = vector - scal*np.dot(housevector,vector.transpose())*housevector
    for i in range(1,n):
      M[i,z] = vector_[0,i-1]
  for r in range(0,n):
    vector = M[r,1:]
    row = vector - scal*np.dot(vector,housevector.transpose())*housevector
    _,l = row.shape
    for x in range(l):
      M[r,x+1] = row[0,x]

  return M


In [12]:
def hessenberg(M):
  n,m = M.shape
  retM = M
  XM = M
  newM = M
  for x in range(n-2):
    newM = householderspiegelung(XM)
    r,c = newM.shape
    for xr in range(r):
      for yc in range(c):
        retM[x+xr,x+yc] = newM[xr,yc]
    XM = newM[1:,1:]
  return retM


In [13]:
def qr3(M, tol=1e-3, maxIter=10000):
  nM = hessenberg(M)
  eigen, errs = qr2(nM, tol, maxIter)
  return eigen, errs

### Ergebnisse

#### A

In [14]:
tol = 1e-4
eigsa1, errsa1 = qr1(A, tol=tol)
eigsa2, errsa2 = qr2(A, tol=tol)
eigsa3, errsa3 = qr3(A, tol=tol)

a:1 b:-8.0, c:16.0, vorne:4.0, unterWurzel:0.0, hinten:0.0


C:\Users\janik\anaconda3\lib\site-packages\ipykernel_launcher.py:35: DeprecationWarning: scipy.sqrt is deprecated and will be removed in SciPy 2.0.0, use numpy.lib.scimath.sqrt instead


In [15]:
print(eigsa1)
print(eigsa2)
print(eigsa3)
print(scl.eigvals(A))

[4.019621656562958, 3.9803783434370414, 1.0000000000000002]
[3.989169822723617, 4.010828632177877, 1.0000015450985065]
[1.0, 4.0, 4.0]
[4.00000002+0.j 3.99999998+0.j 1.        +0.j]


Die Eigenwerte, die die drei QR-Verfahren für Matrix A erhalten, entsprechen den Werten, die die Scipy Methode eigvals zurückgibt.

In [16]:
x1 = np.arange(0,len(errsa1))
x2 = np.arange(0,len(errsa2))
x3 = np.arange(0,len(errsa3))
fig = go.Figure()
fig.add_trace(go.Scatter(x=x1, y=errsa1, mode='lines+markers', name='Error qr1'))
fig.add_trace(go.Scatter(x=x2, y=np.array(errsa2)[:,0], mode='lines+markers', name='Error qr2 real'))
fig.add_trace(go.Scatter(x=x2, y=np.array(errsa2)[:,1], mode='lines+markers', name='Error qr2 imaginary'))
fig.add_trace(go.Scatter(x=x3, y=np.array(errsa3)[:,0], mode='lines+markers', name='Error qr3 real'))
fig.add_trace(go.Scatter(x=x2, y=np.array(errsa3)[:,1], mode='lines+markers', name='Error qr3 imaginary'))
fig.update_layout(title='Errors for matrix A', yaxis_title='Error')
fig.show()

Im oberen Bild deutlich erkennbar ist, dass qr2 und qr3 viel schneller konvergieren als qr1 mit über 200 Iterationen. Mit dem Plot von Plotly ist es einfach, einen Graph unsichtbar zu schalten. So fällt auf, dass die Fehler von qr2 und qr3 übereinander liegen.

#### B

In [17]:
tol = 1e-4
eigsb1, errsb1 = qr1(B, tol=tol)
eigsb2, errsb2 = qr2(B, tol=tol)
eigsb3, errsb3 = qr3(B, tol=tol)

In [18]:
print(eigsb1)
print(eigsb2)
print(eigsb3)
print(scl.eigvals(B))

[3.0282787370890505, 2.9991186839423065, 2.972602578968634]
[3.0217485343837147, 3.0123650642591584, 2.9658864013571216]
[3.0189759977605397, 3.011374958940952, 2.96964904329851]
[3.00001142+1.97801624e-05j 3.00001142-1.97801624e-05j
 2.99997716+0.00000000e+00j]


Hier fällt auf, dass alle QR-Verfahren nur den Realteil der Eigenwerte bestimmen, dieser aber stark mit den eigentlichen Eigenwerten übereinstimmt.

In [19]:
x1 = np.arange(0,len(errsb1))
x2 = np.arange(0,len(errsb2))
x3 = np.arange(0,len(errsb3))
fig = go.Figure()
fig.add_trace(go.Scatter(x=x1, y=errsb1, mode='lines+markers', name='Error qr1'))
fig.add_trace(go.Scatter(x=x2, y=np.array(errsb2)[:,0], mode='lines+markers', name='Error qr2 only real eigenvalues'))
fig.add_trace(go.Scatter(x=x2, y=np.array(errsb2)[:,1], mode='lines+markers', name='Error qr2 only imaginary eigenvalues'))
fig.add_trace(go.Scatter(x=x3, y=np.array(errsb3)[:,0], mode='lines+markers', name='Error qr3 real'))
fig.add_trace(go.Scatter(x=x2, y=np.array(errsb3)[:,1], mode='lines+markers', name='Error qr2 imaginary'))
fig.update_layout(title='Errors for matrix B', yaxis_title='Error')
fig.show()

Auch für Matrix B braucht qr1 über 200 Iterationen, während qr2 und qr3 mit 10 Iterationen fertig sind. Auch hier liegen die Fehler von qr2 und qr3 übereinander.

#### C

In [20]:
tol = 1e-4
maxiter = 10000
eigsc1, errsc1 = qr1(C, tol=tol, maxIter=maxiter)
eigsc2, errsc2 = qr2(C, tol=tol, maxIter=maxiter)
eigsc3, errsc3 = qr3(C, tol=tol, maxIter=maxiter)

a:1 b:6.959703986378013, c:6.865746535207185, vorne:-3.4798519931890066, unterWurzel:20.974493437177266, hinten:2.2898959276120645
a:1 b:-6.959703986378175, c:6.865746535208561, vorne:3.4798519931890874, unterWurzel:20.974493437174015, hinten:2.289895927611887
a:1 b:-3.552713678800501e-15, c:24.999999999999964, vorne:1.7763568394002505e-15, unterWurzel:-99.99999999999986, hinten:4.9999999999999964j
a:1 b:0.0, c:25.00000000000002, vorne:-0.0, unterWurzel:-100.00000000000009, hinten:5.000000000000002j


C:\Users\janik\anaconda3\lib\site-packages\ipykernel_launcher.py:35: DeprecationWarning:

scipy.sqrt is deprecated and will be removed in SciPy 2.0.0, use numpy.lib.scimath.sqrt instead



In [21]:
print(eigsc1)
print(eigsc2)
print(eigsc3)
print(scl.eigvals(C))

[-4.999999957800206, 16.000000153052696, 7.999999969188826, -19.000000164442284]
[-1.1899560655769421, -5.769747920801072, 5.769747920800974, 1.1899560655772006]
[(1.7763568394002505e-15+4.9999999999999964j), (1.7763568394002505e-15-4.9999999999999964j), 5.000000000000002j, (-0-5.000000000000002j)]
[-1.37160031e-07+5.00000008j -1.37160031e-07-5.00000008j
  1.37160044e-07+4.99999992j  1.37160044e-07-4.99999992j]


Bei Matrix C bringt nur qr3 richtige Eigenwerte zurück.

In [22]:
x1 = np.arange(0,len(errsc1))
x2 = np.arange(0,len(errsc2))
x3 = np.arange(0,len(errsc3))
fig = go.Figure()
fig.add_trace(go.Scatter(x=x1, y=errsc1, mode='lines+markers', name='Error qr1'))
fig.add_trace(go.Scatter(x=x2, y=np.array(errsc2)[:,0], mode='lines+markers', name='Error qr2 only real eigenvalues'))
fig.add_trace(go.Scatter(x=x2, y=np.array(errsc2)[:,1], mode='lines+markers', name='Error qr2 only imaginary eigenvalues'))
fig.add_trace(go.Scatter(x=x3, y=np.array(errsc3)[:,0], mode='lines+markers', name='Error qr3 real'))
fig.add_trace(go.Scatter(x=x2, y=np.array(errsc3)[:,1], mode='lines+markers', name='Error qr3 imaginary'))
fig.update_layout(title='Errors for matrix C', yaxis_title='Error')
fig.show()

qr3 ist für Matrix C schon nach 2 Schritten fertig, während qr1 und qr2 keine Lösung finden und nach einer festgelgten Anzahl an Iterationen abbrechen.

#### D

Für Matrix D bringt keiner der QR-Verfahren eine Lösung. qr3 ist nicht durchführbar, da Matrix D nicht in obere Hessenbergform gebracht werden kann.

In [23]:
eigd1, errsd1 = qr1(D, tol=1e-4, maxIter=10000)

In [24]:
eigd2, errsd2 = qr2(D, tol=1e-4, maxIter=10000)

a:1 b:-0.0, c:0.0, vorne:0.0, unterWurzel:0.0, hinten:0.0


C:\Users\janik\anaconda3\lib\site-packages\ipykernel_launcher.py:35: DeprecationWarning:

scipy.sqrt is deprecated and will be removed in SciPy 2.0.0, use numpy.lib.scimath.sqrt instead



In [25]:
print(scl.eigvals(D))
print(eigd1)
print(eigd2)

[0.+1.j 0.-1.j 0.+1.j 0.-1.j]
[0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0]


Die Eigenwerte von Matrix D können also nicht mit dem QR-Verfahren gefunden werden.